In [1]:
# import neccessary library
import tensorflow as tf
import statsmodels.api as sm 
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from sklearn.preprocessing import MinMaxScaler
%matplotlib inline

D:\ProgramData\Anaconda3\lib\site-packages\statsmodels\compat\pandas.py:56: FutureWarning: The pandas.core.datetools module is deprecated and will be removed in a future version. Please use the pandas.tseries module instead.
  from pandas.core import datetools


# 1. Preprocessing Data
# 1.1 Import and Cleansing Data

In [2]:
def read_cleanse_excel(file_name, file_date):
    data = pd.read_excel(file_name)

    # extract date from first column, row 5:end
    date = data.iloc[5:,0].apply(lambda x : pd.to_datetime(file_date + ' ' + str(x)))
    # extract power_kW from 16th column
    power_kW = data.iloc[5:, 16]/1e3

    # create new_frame that is exist only date and power_kW
    new_frame = pd.DataFrame([date,  power_kW])
    new_frame = new_frame.T
    new_frame.columns = ['datetime', 'power_kW']
    new_frame['datetime'] = pd.to_datetime(new_frame['datetime'])
    new_frame = new_frame.set_index(['datetime'])

    # check minor missing data
    if new_frame.shape[0] > 275 and new_frame.shape[0] < 288:
        for i in range(new_frame.shape[0]):
            # identify index of missing data
            dif = (new_frame.index[i+1] - new_frame.index[i]).seconds/60  
            if dif > 5:
                num_mis = round(dif/5 - 1) # amount of missing data

                resolution = (new_frame.iloc[i+1,0] - new_frame.iloc[i,0])/(num_mis+1)

                add_frame = pd.DataFrame({}, columns = ['datetime', 'power_kW'])
                start_new_frame = new_frame.index[i]
                start_new_value = new_frame.iloc[i,0]
                
                for k in range(int(num_mis)):
                    # add delta step 300 sec and value to add_frame
                    start_new_frame = start_new_frame + pd.Timedelta('300 s')
                    start_new_value = start_new_value + resolution
                    
                    add_time = start_new_frame
                    add_value = start_new_value
                    add_frame = pd.concat([add_frame,
                                           pd.DataFrame({'datetime':add_time, 'power_kW':add_value},
                                                        index=[0])])
                # set index to datetime
                add_frame = add_frame.set_index(['datetime'])

                # add add_frame to existing frame and sort by index
                new_frame = pd.concat([new_frame, add_frame])
                new_frame.sort_index(inplace = True)          
        return new_frame, new_frame.shape[0]
    
    # return data immediatly if this day have complete data
    elif new_frame.shape[0] == 288:
        return new_frame, new_frame.shape[0]
    
    # too much value missing return None
    else:
        return None, new_frame.shape[0]

In [3]:
## Retreive all data in the year

date_start = '2013-01-01'
date_temp = date_start
file_name = 'SolarRadiance/' + date_temp + '.xls'

num_stat = []
data, num = read_cleanse_excel(file_name, file_date = date_temp)
num_stat.append(num)

# Loop and import pv data
for i in range(364):
    date_temp = str(pd.to_datetime(date_temp) + pd.Timedelta('1 d'))[0:10]
    print(date_temp)
               
    file_name = 'SolarRadiance/' + date_temp + '.xls'
    data_day, num = read_cleanse_excel(file_name, file_date = date_temp) 
    
    # if data_day is none, it means that too much values are vanish in this day, skip it
    if data_day is not None:
        data = pd.concat([data, data_day])
    num_stat.append(num)
    

2013-01-02
2013-01-03
2013-01-04
2013-01-05
2013-01-06
2013-01-07
2013-01-08
2013-01-09
2013-01-10
2013-01-11
2013-01-12
2013-01-13
2013-01-14
2013-01-15
2013-01-16
2013-01-17
2013-01-18
2013-01-19
2013-01-20
2013-01-21
2013-01-22
2013-01-23
2013-01-24
2013-01-25
2013-01-26
2013-01-27
2013-01-28
2013-01-29
2013-01-30
2013-01-31
2013-02-01
2013-02-02
2013-02-03
2013-02-04
2013-02-05
2013-02-06
2013-02-07
2013-02-08
2013-02-09
2013-02-10
2013-02-11
2013-02-12
2013-02-13
2013-02-14
2013-02-15
2013-02-16
2013-02-17
2013-02-18
2013-02-19
2013-02-20
2013-02-21
2013-02-22
2013-02-23
2013-02-24
2013-02-25
2013-02-26
2013-02-27
2013-02-28
2013-03-01
2013-03-02
2013-03-03
2013-03-04
2013-03-05
2013-03-06
2013-03-07
2013-03-08
2013-03-09
2013-03-10
2013-03-11
2013-03-12
2013-03-13
2013-03-14
2013-03-15
2013-03-16
2013-03-17
2013-03-18
2013-03-19
2013-03-20
2013-03-21
2013-03-22
2013-03-23
2013-03-24
2013-03-25
2013-03-26
2013-03-27
2013-03-28
2013-03-29
2013-03-30
2013-03-31
2013-04-01
2013-04-02

# 1.2 Check remained missing data

In [4]:
new_frame = data.copy()
is_missing = False

for i in range(new_frame.shape[0] - 1):
            # identify index of missing data
            dif = (new_frame.index[i+1] - new_frame.index[i]).seconds/60
            if dif > 5:
                num_mis = dif/5 - 1 # amount of missing data
                print('Time i\t\t',new_frame.index[i])
                print('Time i+1\t',new_frame.index[i+1])
                
                is_missing = True

# 1.3 Remove night time 

In [5]:
# Observe some data
data.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 103968 entries, 2013-01-01 00:00:00 to 2013-12-31 23:55:00
Data columns (total 1 columns):
power_kW    51241 non-null float64
dtypes: float64(1)
memory usage: 1.6 MB


In [6]:
# Observe some data
data = data.fillna(0)
data.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 103968 entries, 2013-01-01 00:00:00 to 2013-12-31 23:55:00
Data columns (total 1 columns):
power_kW    103968 non-null float64
dtypes: float64(1)
memory usage: 1.6 MB


In [ ]:
## Define night time by --> set(whole_day_time) - set(day_time)
'''
This cell will calculate result dataframe which merge is_daytime boolean
'''
# Group data by day
data_grouped = data.groupby(pd.Grouper(freq='D'))
group_keys = data_grouped.groups.keys()

date_start = pd.to_datetime('2013-01-01 00:00:00')
pv_day = data_grouped.get_group(date_start)
day_time = pv_day != 0

count = 0
for key in group_keys:
    
    # Some day is missing and raise an error if key is the missing day
    # so except that missing day using try, except
    try:
        pv_day_temp = data_grouped.get_group(key)
        
        # find first and last index of day time for every day
        for i in range(288):
            if abs(pv_day_temp.iloc[i,0]) > 10e-4:
                first_index = i
                break
        for i in range(287,-1,-1):
            if abs(pv_day_temp.iloc[i,0]) > 10e-4:
                last_index = i
                break
        
        day_time = pv_day_temp.copy()
        # Define is_daytime
        day_time.iloc[first_index:last_index,0] = True
        day_time.iloc[:first_index-1,0] = False
        day_time.iloc[last_index-1:,0] = False
        
        # merge is_daytime to data
        day_time.index = pv_day_temp.index
        day_time.columns = ['is_daytime']
        
        if count == 0:
            result = pd.merge(pv_day_temp, day_time, left_index=True, right_index=True)
        else:
            result = pd.concat([result,
                                pd.merge(pv_day_temp, day_time, left_index=True, right_index=True)])
        count += 1
    except KeyError:
        pass

## Visualize result
result

power_kW is_daytime
datetime                                
2013-01-01 00:00:00       0.0      False
2013-01-01 00:05:00       0.0      False
2013-01-01 00:10:00       0.0      False
2013-01-01 00:15:00       0.0      False
2013-01-01 00:20:00       0.0      False
2013-01-01 00:25:00       0.0      False
2013-01-01 00:30:00       0.0      False
2013-01-01 00:35:00       0.0      False
2013-01-01 00:40:00       0.0      False
2013-01-01 00:45:00       0.0      False
2013-01-01 00:50:00       0.0      False
2013-01-01 00:55:00       0.0      False
2013-01-01 01:00:00       0.0      False
2013-01-01 01:05:00       0.0      False
2013-01-01 01:10:00       0.0      False
2013-01-01 01:15:00       0.0      False
2013-01-01 01:20:00       0.0      False
2013-01-01 01:25:00       0.0      False
2013-01-01 01:30:00       0.0      False
2013-01-01 01:35:00       0.0      False
2013-01-01 01:40:00       0.0      False
2013-01-01 01:45:00       0.0      False
2013-01-01 01:50:00       0.0      False
2013-01-01 01:55:00       0.0      False
2013-01-01 02:00:00       0.0      False
2013-01-01 02:05:00       0.0      False
2013-01-01 02:10:00       0.0      False
2013-01-01 02:15:00       0.0      False
2013-01-01 02:20:00       0.0      False
2013-01-01 02:25:00       0.0      False
...                       ...        ...
2013-12-31 21:30:00       0.0      False
2013-12-31 21:35:00       0.0      False
2013-12-31 21:40:00       0.0      False
2013-12-31 21:45:00       0.0      False
2013-12-31 21:50:00       0.0      False
2013-12-31 21:55:00       0.0      False
2013-12-31 22:00:00       0.0      False
2013-12-31 22:05:00       0.0      False
2013-12-31 22:10:00       0.0      False
2013-12-31 22:15:00       0.0      False
2013-12-31 22:20:00       0.0      False
2013-12-31 22:25:00       0.0      False
2013-12-31 22:30:00       0.0      False
2013-12-31 22:35:00       0.0      False
2013-12-31 22:40:00       0.0      False
2013-12-31 22:45:00       0.0      False
2013-12-31 22:50:00       0.0      False
2013-12-31 22:55:00       0.0      False
2013-12-31 23:00:00       0.0      False
2013-12-31 23:05:00       0.0      False
2013-12-31 23:10:00       0.0      False
2013-12-31 23:15:00       0.0      False
2013-12-31 23:20:00       0.0      False
2013-12-31 23:25:00       0.0      False
2013-12-31 23:30:00       0.0      False
2013-12-31 23:35:00       0.0      False
2013-12-31 23:40:00       0.0      False
2013-12-31 23:45:00       0.0      False
2013-12-31 23:50:00       0.0      False
2013-12-31 23:55:00       0.0      False

[103968 rows x 2 columns]

In [ ]:
'''
Now it's time to remove night time by remove False row of is_daytime columns!
'''
# Group result data by day
data_daytime = result.loc[result['is_daytime']==True,:]
for i in range(len(data_daytime)):
    print(data_daytime.iloc[i,:])

power_kW      0.02779
is_daytime       True
Name: 2013-01-01 07:30:00, dtype: object
power_kW      0.04902
is_daytime       True
Name: 2013-01-01 07:35:00, dtype: object
power_kW      0.07209
is_daytime       True
Name: 2013-01-01 07:40:00, dtype: object
power_kW      0.09013
is_daytime       True
Name: 2013-01-01 07:45:00, dtype: object
power_kW      0.10483
is_daytime       True
Name: 2013-01-01 07:50:00, dtype: object
power_kW      0.11588
is_daytime       True
Name: 2013-01-01 07:55:00, dtype: object
power_kW      0.15139
is_daytime       True
Name: 2013-01-01 08:00:00, dtype: object
power_kW      0.17766
is_daytime       True
Name: 2013-01-01 08:05:00, dtype: object
power_kW      0.2468
is_daytime      True
Name: 2013-01-01 08:10:00, dtype: object
power_kW      0.29613
is_daytime       True
Name: 2013-01-01 08:15:00, dtype: object
power_kW      0.2903
is_daytime      True
Name: 2013-01-01 08:20:00, dtype: object
power_kW      0.25008
is_daytime       True
Name: 2013-01-01 08:25:00

power_kW      0.40079
is_daytime       True
Name: 2013-01-01 16:10:00, dtype: object
power_kW      0.37775
is_daytime       True
Name: 2013-01-01 16:15:00, dtype: object
power_kW      0.34109
is_daytime       True
Name: 2013-01-01 16:20:00, dtype: object
power_kW      0.31743
is_daytime       True
Name: 2013-01-01 16:25:00, dtype: object
power_kW      0.2966
is_daytime      True
Name: 2013-01-01 16:30:00, dtype: object
power_kW      0.27852
is_daytime       True
Name: 2013-01-01 16:35:00, dtype: object
power_kW      0.23355
is_daytime       True
Name: 2013-01-01 16:40:00, dtype: object
power_kW      0.20518
is_daytime       True
Name: 2013-01-01 16:45:00, dtype: object
power_kW      0.20764
is_daytime       True
Name: 2013-01-01 16:50:00, dtype: object
power_kW      0.17273
is_daytime       True
Name: 2013-01-01 16:55:00, dtype: object
power_kW      0.14705
is_daytime       True
Name: 2013-01-01 17:00:00, dtype: object
power_kW      0.13118
is_daytime       True
Name: 2013-01-01 17:05:

Name: 2013-01-02 15:05:00, dtype: object
power_kW      0.62187
is_daytime       True
Name: 2013-01-02 15:10:00, dtype: object
power_kW      0.60389
is_daytime       True
Name: 2013-01-02 15:15:00, dtype: object
power_kW      0.56943
is_daytime       True
Name: 2013-01-02 15:20:00, dtype: object
power_kW      0.56672
is_daytime       True
Name: 2013-01-02 15:25:00, dtype: object
power_kW      0.54256
is_daytime       True
Name: 2013-01-02 15:30:00, dtype: object
power_kW      0.51226
is_daytime       True
Name: 2013-01-02 15:35:00, dtype: object
power_kW      0.48905
is_daytime       True
Name: 2013-01-02 15:40:00, dtype: object
power_kW      0.48392
is_daytime       True
Name: 2013-01-02 15:45:00, dtype: object
power_kW      0.43954
is_daytime       True
Name: 2013-01-02 15:50:00, dtype: object
power_kW      0.43369
is_daytime       True
Name: 2013-01-02 15:55:00, dtype: object
power_kW      0.43198
is_daytime       True
Name: 2013-01-02 16:00:00, dtype: object
power_kW      0.40885
is

Name: 2013-01-03 14:55:00, dtype: object
power_kW      0.62084
is_daytime       True
Name: 2013-01-03 15:00:00, dtype: object
power_kW      0.60353
is_daytime       True
Name: 2013-01-03 15:05:00, dtype: object
power_kW      0.4242
is_daytime      True
Name: 2013-01-03 15:10:00, dtype: object
power_kW      0.38151
is_daytime       True
Name: 2013-01-03 15:15:00, dtype: object
power_kW      0.17933
is_daytime       True
Name: 2013-01-03 15:20:00, dtype: object
power_kW      0.20376
is_daytime       True
Name: 2013-01-03 15:25:00, dtype: object
power_kW      0.33456
is_daytime       True
Name: 2013-01-03 15:30:00, dtype: object
power_kW      0.58305
is_daytime       True
Name: 2013-01-03 15:35:00, dtype: object
power_kW      0.58622
is_daytime       True
Name: 2013-01-03 15:40:00, dtype: object
power_kW      0.55787
is_daytime       True
Name: 2013-01-03 15:45:00, dtype: object
power_kW      0.51834
is_daytime       True
Name: 2013-01-03 15:50:00, dtype: object
power_kW      0.48383
is_d

power_kW      0.2746
is_daytime      True
Name: 2013-01-04 14:50:00, dtype: object
power_kW      0.26869
is_daytime       True
Name: 2013-01-04 14:55:00, dtype: object
power_kW      0.26852
is_daytime       True
Name: 2013-01-04 15:00:00, dtype: object
power_kW      0.25704
is_daytime       True
Name: 2013-01-04 15:05:00, dtype: object
power_kW      0.25954
is_daytime       True
Name: 2013-01-04 15:10:00, dtype: object
power_kW      0.27786
is_daytime       True
Name: 2013-01-04 15:15:00, dtype: object
power_kW      0.26406
is_daytime       True
Name: 2013-01-04 15:20:00, dtype: object
power_kW      0.27792
is_daytime       True
Name: 2013-01-04 15:25:00, dtype: object
power_kW      0.25707
is_daytime       True
Name: 2013-01-04 15:30:00, dtype: object
power_kW      0.24257
is_daytime       True
Name: 2013-01-04 15:35:00, dtype: object
power_kW      0.23441
is_daytime       True
Name: 2013-01-04 15:40:00, dtype: object
power_kW      0.23671
is_daytime       True
Name: 2013-01-04 15:45:

...

power_kW      0.89793
is_daytime       True
Name: 2013-11-17 11:55:00, dtype: object
power_kW      0.70016
is_daytime       True
Name: 2013-11-17 12:00:00, dtype: object
power_kW      0.4733
is_daytime      True
Name: 2013-11-17 12:05:00, dtype: object
power_kW      0.84438
is_daytime       True
Name: 2013-11-17 12:10:00, dtype: object
power_kW      0.85461
is_daytime       True
Name: 2013-11-17 12:15:00, dtype: object
power_kW      0.87998
is_daytime       True
Name: 2013-11-17 12:20:00, dtype: object
power_kW      0.75276
is_daytime       True
Name: 2013-11-17 12:25:00, dtype: object
power_kW      0.90113
is_daytime       True
Name: 2013-11-17 12:30:00, dtype: object
power_kW      0.97211
is_daytime       True
Name: 2013-11-17 12:35:00, dtype: object
power_kW      1.00509
is_daytime       True
Name: 2013-11-17 12:40:00, dtype: object
power_kW      1.06929
is_daytime       True
Name: 2013-11-17 12:45:00, dtype: object
power_kW      0.88963
is_daytime       True
Name: 2013-11-17 12:50:

power_kW      0.87524
is_daytime       True
Name: 2013-11-18 11:40:00, dtype: object
power_kW      0.8632
is_daytime      True
Name: 2013-11-18 11:45:00, dtype: object
power_kW      0.9306
is_daytime      True
Name: 2013-11-18 11:50:00, dtype: object
power_kW      0.5932
is_daytime      True
Name: 2013-11-18 11:55:00, dtype: object
power_kW      0.62676
is_daytime       True
Name: 2013-11-18 12:00:00, dtype: object
power_kW      0.58355
is_daytime       True
Name: 2013-11-18 12:05:00, dtype: object
power_kW      0.82228
is_daytime       True
Name: 2013-11-18 12:10:00, dtype: object
power_kW      0.83928
is_daytime       True
Name: 2013-11-18 12:15:00, dtype: object
power_kW      0.96154
is_daytime       True
Name: 2013-11-18 12:20:00, dtype: object
power_kW      0.91927
is_daytime       True
Name: 2013-11-18 12:25:00, dtype: object
power_kW      0.91216
is_daytime       True
Name: 2013-11-18 12:30:00, dtype: object
power_kW      0.91431
is_daytime       True
Name: 2013-11-18 12:35:00, 

power_kW      0.84635
is_daytime       True
Name: 2013-11-19 11:50:00, dtype: object
power_kW      0.82482
is_daytime       True
Name: 2013-11-19 11:55:00, dtype: object
power_kW      0.89904
is_daytime       True
Name: 2013-11-19 12:00:00, dtype: object
power_kW      0.90361
is_daytime       True
Name: 2013-11-19 12:05:00, dtype: object
power_kW      0.72129
is_daytime       True
Name: 2013-11-19 12:10:00, dtype: object
power_kW      0.48918
is_daytime       True
Name: 2013-11-19 12:15:00, dtype: object
power_kW      0.80469
is_daytime       True
Name: 2013-11-19 12:20:00, dtype: object
power_kW      0.76902
is_daytime       True
Name: 2013-11-19 12:25:00, dtype: object
power_kW      0.8552
is_daytime      True
Name: 2013-11-19 12:30:00, dtype: object
power_kW      0.85941
is_daytime       True
Name: 2013-11-19 12:35:00, dtype: object
power_kW      0.84846
is_daytime       True
Name: 2013-11-19 12:40:00, dtype: object
power_kW      0.67164
is_daytime       True
Name: 2013-11-19 12:45:

power_kW      0.65422
is_daytime       True
Name: 2013-11-20 11:40:00, dtype: object
power_kW      0.47011
is_daytime       True
Name: 2013-11-20 11:45:00, dtype: object
power_kW      0.4338
is_daytime      True
Name: 2013-11-20 11:50:00, dtype: object
power_kW      0.26596
is_daytime       True
Name: 2013-11-20 11:55:00, dtype: object
power_kW      0.32251
is_daytime       True
Name: 2013-11-20 12:00:00, dtype: object
power_kW      0.18538
is_daytime       True
Name: 2013-11-20 12:05:00, dtype: object
power_kW      0.21407
is_daytime       True
Name: 2013-11-20 12:10:00, dtype: object
power_kW      0.39496
is_daytime       True
Name: 2013-11-20 12:15:00, dtype: object
power_kW      0.24261
is_daytime       True
Name: 2013-11-20 12:20:00, dtype: object
power_kW      0.19089
is_daytime       True
Name: 2013-11-20 12:25:00, dtype: object
power_kW      0.20547
is_daytime       True
Name: 2013-11-20 12:30:00, dtype: object
power_kW      0.25449
is_daytime       True
Name: 2013-11-20 12:35:

power_kW      0.56231
is_daytime       True
Name: 2013-11-21 12:25:00, dtype: object
power_kW      0.592
is_daytime     True
Name: 2013-11-21 12:30:00, dtype: object
power_kW      0.64893
is_daytime       True
Name: 2013-11-21 12:35:00, dtype: object
power_kW      0.75867
is_daytime       True
Name: 2013-11-21 12:40:00, dtype: object
power_kW      0.67754
is_daytime       True
Name: 2013-11-21 12:45:00, dtype: object
power_kW      0.3514
is_daytime      True
Name: 2013-11-21 12:50:00, dtype: object
power_kW      0.52763
is_daytime       True
Name: 2013-11-21 12:55:00, dtype: object
power_kW      0.74253
is_daytime       True
Name: 2013-11-21 13:00:00, dtype: object
power_kW      0.48145
is_daytime       True
Name: 2013-11-21 13:05:00, dtype: object
power_kW      0.34284
is_daytime       True
Name: 2013-11-21 13:10:00, dtype: object
power_kW      0.20338
is_daytime       True
Name: 2013-11-21 13:15:00, dtype: object
power_kW      0.2385
is_daytime      True
Name: 2013-11-21 13:20:00, dt

In [ ]:
data_daytime.iloc[:150,:].plot(y=['power_kW'])